In [ ]:
import pandas as pd
import requests
import zipfile
import io
import os
import shutil
from PIL import Image as PILImage, ImageFile
from tqdm import tqdm
from datasets import Dataset, Features, Value, Image, load_dataset
from huggingface_hub import login, HfApi
import cv2
import concurrent.futures
import csv

In [ ]:
# Allow loading of truncated images
ImageFile.LOAD_TRUNCATED_IMAGES = True

In [ ]:
def read_excel_and_get_urls(excel_file):
    """
    Read Excel file and extract URLs, tilenames, and zones
    
    Args:
        excel_file: Path to Excel file
    
    Returns:
        DataFrame with TILENAME, ZONE, URL columns
    """
    print(f"Reading Excel file: {excel_file}")
    df = pd.read_excel(excel_file)
    
    # Ensure expected columns exist
    required_columns = ['TILENAME', 'ZONE', 'URL']
    for col in required_columns:
        if col not in df.columns:
            raise ValueError(f"Required column '{col}' not found in Excel file.")
    
    print(f"Found {len(df)} entries in Excel file")
    return df

def extract_filename_from_url(url):
    """
    Extract the base filename from the URL
    
    Args:
        url: URL of the zip file
    
    Returns:
        Base filename without extension
    """
    # Extract filename from URL
    # This may need adjustment based on the URL format
    filename = url.split('/')[-1]
    # Remove .zip extension if present
    if filename.lower().endswith('.zip'):
        filename = os.path.splitext(filename)[0]
    return filename


def download_and_extract_jp2(tilename, zone, url, jp2_dir):
    """
    Download a zip file from the given URL and extract only the JP2 image file
    
    Args:
        tilename: Name of the tile
        zone: Zone identifier
        url: URL to the zip file
        jp2_dir: Directory to save JP2 images
    
    Returns:
        Dictionary with image information (jp2_path, tilename, zone)
    """
    try:
        # Download the zip file
        response = requests.get(url, stream=True)
        
        if response.status_code != 200:
            print(f"Failed to download {tilename}: {response.status_code}")
            return None
        
        # Ensure JP2 directory exists
        os.makedirs(jp2_dir, exist_ok=True)
        
        # Extract image files
        with zipfile.ZipFile(io.BytesIO(response.content)) as zip_ref:
            # Get all files in the zip
            all_files = zip_ref.namelist()
            
            # Filter for JP2 image files
            jp2_files = [f for f in all_files if f.lower().endswith('.jp2')]
            
            if not jp2_files:
                print(f"No JP2 files found in {tilename} zip")
                return None
            
            # Get the first JP2 file (assuming one image per zip)
            jp2_file = jp2_files[0]
            jp2_filename = os.path.basename(jp2_file)
            jp2_path = os.path.join(jp2_dir, jp2_filename)
            
            # Extract JP2 file
            with zip_ref.open(jp2_file) as source, open(jp2_path, 'wb') as target:
                shutil.copyfileobj(source, target)
            
            return {
                "jp2_path": jp2_path,
                "tilename": tilename,
                "zone": zone
            }
            
    except Exception as e:
        print(f"Error processing {tilename}: {e}")
        return None
    
def process_file(jp2_path, jpeg_path):
    try:
        # Read JP2 image
        img = cv2.imread(jp2_path)
        
        # Check if the image is read properly
        if img is None:
            print(f"Error reading {jp2_path}, skipping.")
            return
            
        # Save as JPEG
        cv2.imwrite(jpeg_path, img, [int(cv2.IMWRITE_JPEG_QUALITY), 95])
    except Exception as e:
        print(f"Error converting {jp2_path}: {e}")

def convert_jp2_to_jpeg(jp2_dir, jpeg_dir, max_workers=4):
    """
    Convert all JP2 files in a directory to JPEG using OpenCV with multithreading.
    
    Args:
        jp2_dir: Directory containing JP2 files
        jpeg_dir: Directory to save converted JPEG images
        max_workers: Number of threads to use for processing
    """
    # Ensure output directory exists
    os.makedirs(jpeg_dir, exist_ok=True)
    
    # Get all JP2 files
    input_files = [f for f in os.listdir(jp2_dir) if f.lower().endswith('.jp2') and f != '.DS_Store']
    
    print(f"Found {len(input_files)} JP2 files to convert")
    
    # Prepare task list
    tasks = []
    for f in input_files:
        jp2_path = os.path.join(jp2_dir, f)
        jpeg_filename = os.path.splitext(f)[0] + ".jpg"
        jpeg_path = os.path.join(jpeg_dir, jpeg_filename)
        
        # Skip if already processed
        if os.path.isfile(jpeg_path):
            print(f"Already processed: {f}")
            continue
            
        tasks.append((jp2_path, jpeg_path))
    
    # Process files in parallel
    with concurrent.futures.ThreadPoolExecutor(max_workers=max_workers) as executor:
        list(tqdm(executor.map(lambda args: process_file(*args), tasks), total=len(tasks), desc="Converting JP2 to JPEG"))

def convert_jp2_to_jpeg(jp2_dir, jpeg_dir):
    """
    Convert all JP2 files in a directory to JPEG using OpenCV.
    
    Args:
        jp2_dir: Directory containing JP2 files
        jpeg_dir: Directory to save converted JPEG images
    """
    # Ensure output directory exists
    os.makedirs(jpeg_dir, exist_ok=True)
    
    # Get all JP2 files
    input_files = [f for f in os.listdir(jp2_dir) if f.lower().endswith('.jp2') and f != '.DS_Store']
    
    print(f"Found {len(input_files)} JP2 files to convert")
    
    # Process files
    for f in tqdm(input_files, desc="Converting JP2 to JPEG"):
        try:
            jp2_path = os.path.join(jp2_dir, f)
            jpeg_filename = os.path.splitext(f)[0] + ".jpg"
            jpeg_path = os.path.join(jpeg_dir, jpeg_filename)
            
            # Skip if already processed
            if os.path.isfile(jpeg_path):
                print(f"Already processed: {f}")
                continue
                
            # Read JP2 image
            img = cv2.imread(jp2_path)
            
            # Check if the image is read properly
            if img is None:
                print(f"Error reading {f}, skipping.")
                continue
                
            # Save as JPEG
            cv2.imwrite(jpeg_path, img, [int(cv2.IMWRITE_JPEG_QUALITY), 95])
        except Exception as e:
            print(f"Error converting {f}: {e}")

def convert_jp2_to_jpeg(jp2_dir, jpeg_dir):
    """
    Convert all JP2 files in a directory to JPEG
    
    Args:
        jp2_dir: Directory containing JP2 files
        jpeg_dir: Directory to save converted JPEG images
    """
    # Ensure directories exist
    if not os.path.exists(jpeg_dir):
        os.makedirs(jpeg_dir)
    if not os.path.exists(jp2_dir):
        os.makedirs(jp2_dir)
    
    # Get all JP2 files
    input_files = os.listdir(jp2_dir)
    input_files = [f for f in input_files if f.lower().endswith('.jp2') and f != '.DS_Store']
    
    print(f"Found {len(input_files)} JP2 files to convert")
    
    # Process files one by one
    for f in tqdm(input_files, desc="Converting JP2 to JPEG"):
        try:
            jp2_path = os.path.join(jp2_dir, f)
            jpeg_filename = os.path.splitext(f)[0] + ".jpg"
            jpeg_path = os.path.join(jpeg_dir, jpeg_filename)
            
            # Skip if already processed
            if os.path.isfile(jpeg_path):
                print(f"Already processed: {f}")
                continue
                
            # Open and convert the image
            im = PILImage.open(jp2_path)
            if im.mode != 'RGB':
                im = im.convert('RGB')
            
            # Save as JPEG
            im.save(jpeg_path, 'JPEG', quality=95)
            im.close()
        except Exception as e:
            print(f"Error converting {f}: {e}")

def recreate_image_info_list(excel_file, jpeg_dir):
    """
    Recreate image_info_list by matching jpeg files with Excel entries
    
    Args:
        excel_file: Path to Excel file
        jpeg_dir: Directory containing JPEG files
    
    Returns:
        List of dictionaries with image information
    """
    # Read Excel file
    df = read_excel_and_get_urls(excel_file)
    
    # Create mapping from filename to tilename and zone
    filename_to_metadata = {}
    
    # Try different approaches to match filenames
    for _, row in df.iterrows():
        tilename = row['TILENAME']
        zone = row['ZONE']
        url = row['URL']
        
        # Extract filename from URL as a potential match criterion
        extracted_filename = extract_filename_from_url(url)
        filename_to_metadata[extracted_filename] = {'tilename': tilename, 'zone': zone}
        
        # Also map the tilename directly as another potential match
        filename_to_metadata[tilename] = {'tilename': tilename, 'zone': zone}
    
    # Get all JPEG files
    jpeg_files = [f for f in os.listdir(jpeg_dir) if f.lower().endswith('.jpg') or f.lower().endswith('.jpeg')]
    print(f"Found {len(jpeg_files)} JPEG files in the directory")
    
    # Match JPEG files to metadata
    image_info_list = []
    unmatched_files = []
    
    for jpeg_file in tqdm(jpeg_files, desc="Matching JPEG files to metadata"):
        jpeg_path = os.path.join(jpeg_dir, jpeg_file)
        base_name = os.path.splitext(jpeg_file)[0]
        
        # Try different matching strategies
        metadata = None
        
        # Direct match with the extracted filename
        if base_name in filename_to_metadata:
            metadata = filename_to_metadata[base_name]
        else:
            # Try partial matches
            matched_keys = [key for key in filename_to_metadata.keys() if key in base_name or base_name in key]
            if matched_keys:
                # Use the first match if multiple found
                metadata = filename_to_metadata[matched_keys[0]]
        
        if metadata:
            image_info_list.append({
                "path": jpeg_path,
                "tilename": metadata['tilename'],
                "zone": metadata['zone']
            })
        else:
            unmatched_files.append(jpeg_file)
    
    print(f"Successfully matched {len(image_info_list)} JPEG files with metadata")
    
    if unmatched_files:
        print(f"Warning: Could not match {len(unmatched_files)} files with metadata")
        if len(unmatched_files) < 10:
            print("Unmatched files:", unmatched_files)
        else:
            print("First 10 unmatched files:", unmatched_files[:10])
    
    return image_info_list


def organize_images_for_imagefolder(excel_file, jpeg_dir, output_dir, rename_instead_of_copy=True):
    """
    Organize images and create metadata for ImageFolder format
    
    Args:
        excel_file: Path to Excel file with metadata
        jpeg_dir: Directory containing JPEG files
        output_dir: Directory to save organized images and metadata
        rename_instead_of_copy: If True, rename/move files instead of copying them
    
    Returns:
        Path to the organized dataset directory
    """
    print(f"Reading Excel file: {excel_file}")
    df = pd.read_excel(excel_file)
    
    # Ensure required columns exist
    required_columns = ['TILENAME', 'ZONE', 'URL']
    for col in required_columns:
        if col not in df.columns:
            raise ValueError(f"Required column '{col}' not found in Excel file.")
    
    # Use the JPEG directory as the train directory if we're renaming
    if rename_instead_of_copy:
        # Create parent directory if it doesn't exist
        os.makedirs(output_dir, exist_ok=True)
        
        # Just rename the jpeg_dir to be inside the output_dir
        train_dir = os.path.join(output_dir, "train")
        
        # If the train directory already exists but is different from jpeg_dir, handle it
        if os.path.exists(train_dir) and os.path.abspath(train_dir) != os.path.abspath(jpeg_dir):
            response = input(f"Train directory {train_dir} already exists. Do you want to replace it? (yes/no): ")
            if response.lower() == 'yes':
                shutil.rmtree(train_dir)
            else:
                print("Using existing train directory.")
                
        # If train_dir doesn't exist, rename jpeg_dir to train_dir
        if not os.path.exists(train_dir):
            print(f"Renaming directory {jpeg_dir} to {train_dir}")
            shutil.move(jpeg_dir, train_dir)
        # If jpeg_dir is already the train_dir, do nothing
        elif os.path.abspath(train_dir) == os.path.abspath(jpeg_dir):
            print(f"JPEG directory is already {train_dir}, no renaming needed")
    else:
        # Create the output directory structure for copying
        os.makedirs(output_dir, exist_ok=True)
        train_dir = os.path.join(output_dir, "train")
        os.makedirs(train_dir, exist_ok=True)
    
    # Get all JPEG files
    jpeg_files = [f for f in os.listdir(train_dir) if f.lower().endswith('.jpg') or f.lower().endswith('.jpeg')]
    print(f"Found {len(jpeg_files)} JPEG files")
    
    # Create a mapping of filename to metadata
    filename_to_metadata = {}
    for _, row in df.iterrows():
        tilename = row['TILENAME']
        zone = row['ZONE']
        # Use both the full tilename and the base name for matching
        filename_to_metadata[tilename] = {'tilename': tilename, 'zone': zone}
        filename_to_metadata[os.path.basename(tilename)] = {'tilename': tilename, 'zone': zone}
    
    # Create metadata.csv file
    metadata_path = os.path.join(train_dir, "metadata.csv")
    with open(metadata_path, 'w', newline='') as csvfile:
        fieldnames = ['file_name', 'tilename', 'zone']
        writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
        writer.writeheader()
        
        # Add files to metadata
        successful_matches = 0
        for jpeg_file in tqdm(jpeg_files, desc="Creating metadata for images"):
            # Try to match the image to metadata
            base_name = os.path.splitext(jpeg_file)[0]
            
            # Find matching metadata using different strategies
            metadata = None
            if base_name in filename_to_metadata:
                metadata = filename_to_metadata[base_name]
            else:
                # Try partial matches
                matched_keys = [key for key in filename_to_metadata.keys() 
                                if key in base_name or base_name in key]
                if matched_keys:
                    metadata = filename_to_metadata[matched_keys[0]]
            
            if metadata:
                # Add to metadata.csv
                writer.writerow({
                    'file_name': jpeg_file,
                    'tilename': metadata['tilename'],
                    'zone': metadata['zone']
                })
                successful_matches += 1
            else:
                print(f"Could not find metadata for {jpeg_file}")
        
        print(f"Successfully matched {successful_matches} images with metadata")
    
    return output_dir

def upload_dataset_to_hub(dataset_dir, repo_name):
    """
    Upload the dataset to the Hugging Face Hub
    
    Args:
        dataset_dir: Directory containing the organized dataset
        repo_name: Name of the repository on Hugging Face Hub
    """
    # Load the dataset using ImageFolder
    print(f"Loading dataset from {dataset_dir}")
    dataset = load_dataset("imagefolder", data_dir=dataset_dir)
    
    # Push to Hugging Face Hub
    print(f"Pushing dataset to Hugging Face Hub: {repo_name}")
    dataset.push_to_hub(repo_name)
    print("Dataset uploaded successfully!")


In [ ]:
# Excel file path
excel_file = "/fsx/avijit/projects/datacommonsMA/massgis_2023_aerial_imagery/COQ2023INDEX_POLY.xlsx"

# Define directories
base_dir = "/fsx/avijit/projects/datacommonsMA/massgis_2023_aerial_imagery"
output_dir = "/fsx/avijit/projects/datacommonsMA/massgis_2023_aerial_imagery/imagefolder-dataset"

jp2_dir = os.path.join(base_dir, "jp2-files")
jpeg_dir = os.path.join(base_dir, "jpeg-files")

# Ensure directories exist
os.makedirs(jp2_dir, exist_ok=True)
os.makedirs(jpeg_dir, exist_ok=True)

Step 1: Read Excel file
print("Step 1: Reading Excel file")
df = read_excel_and_get_urls(excel_file)

# Step 2: Download and extract JP2 files
print("Step 2: Downloading and extracting JP2 files")
jp2_info_list = []

for idx, row in tqdm(df.iterrows(), total=len(df), desc="Downloading ZIP files"):
    tilename = row['TILENAME']
    zone = row['ZONE']
    url = row['URL']
    
    info = download_and_extract_jp2(tilename, zone, url, jp2_dir)
    if info is not None:
        jp2_info_list.append(info)

print(f"Successfully downloaded {len(jp2_info_list)} JP2 files")

# Step 3: Batch convert JP2 to JPEG
print("Step 3: Converting JP2 to JPEG")
convert_jp2_to_jpeg(jp2_dir, jpeg_dir)

#Step 4: Create image info list for dataset creation
print("Step 4: Creating image info list")
image_info_list = recreate_image_info_list(excel_file, jpeg_dir)
    
print(f"Found {len(image_info_list)} matched JPEG files")

# Step 5: Delete JP2 files to save space
print("Step 5: Deleting JP2 files...")
shutil.rmtree(jp2_dir)
print("JP2 files deleted")
    

Step 4: Creating image info list
Reading Excel file: /fsx/avijit/projects/datacommonsMA/massgis_2023_aerial_imagery/COQ2023INDEX_POLY.xlsx
Found 10218 entries in Excel file
Found 10218 JPEG files in the directory


Matching JPEG files to metadata: 100%|█████████████████| 10218/10218 [00:00<00:00, 616174.46it/s]

Successfully matched 10218 JPEG files with metadata
Found 10218 matched JPEG files
Step 5: Deleting JP2 files...


JP2 files deleted


In [ ]:
# Login to Hugging Face (use your API token)
api_token = input("Enter your Hugging Face API token: ")
login(token=api_token)


# Create and push Hugging Face dataset
hf_dataset_name = input("Enter the name for your Hugging Face dataset (username/dataset-name): ")
upload_dataset_to_hub(image_info_list, hf_dataset_name)

print("Done!")

In [22]:
import os
import pandas as pd
import pyarrow as pa
import pyarrow.parquet as pq
from PIL import Image as PILImage
import numpy as np
from tqdm import tqdm
import io

# Import the pandas_image_methods library
from pandas_image_methods import PILMethods

# Register the PIL methods accessor
pd.api.extensions.register_series_accessor("pil")(PILMethods)

base_dir = "/fsx/avijit/projects/datacommonsMA/massgis_2023_aerial_imagery/imagefolder-dataset"
train_dir = os.path.join(base_dir, "train")
output_dir = os.path.join(base_dir, "data")
output_path = os.path.join(output_dir, "sample_dataset_256x256.parquet")

# Create the output directory if it doesn't exist
os.makedirs(output_dir, exist_ok=True)

target_size = (256, 256)
num_samples = 50

metadata_path = os.path.join(train_dir, "metadata.csv")
print(f"Reading metadata from {metadata_path}")
metadata_df = pd.read_csv(metadata_path)

# Take a random sample of 50 rows
if len(metadata_df) > num_samples:
    metadata_df = metadata_df.sample(n=num_samples, random_state=42)

print(f"Selected {len(metadata_df)} samples")

# Create DataFrame with just the paths first
df = pd.DataFrame({
    'file_path': [os.path.join(train_dir, row['file_name']) for _, row in metadata_df.iterrows()],
    'tilename': metadata_df['tilename'].tolist(),
    'zone': metadata_df['zone'].astype('int64').tolist()
})

# Load images using the pil accessor
print("Loading and resizing images...")
df['image'] = df['file_path'].pil.open()

# Resize the images
print("Resizing images...")
df['image'] = df['image'].pil.resize(target_size)

# Keep only the required columns for the preview
df = df[['image', 'tilename', 'zone']]

# Save to Parquet (the library will handle the PIL images correctly)
print(f"Saving to {output_path}...")
df.to_parquet(output_path)

print(f"Saved sample dataset to {output_path}")
print(f"File size: {os.path.getsize(output_path) / (1024 * 1024):.2f} MB")

# Verify the saved file
print("Verifying saved file...")
df_check = pd.read_parquet(output_path)
print("Columns in saved file:", df_check.columns.tolist())
print("Number of rows:", len(df_check))

Reading metadata from /fsx/avijit/projects/datacommonsMA/massgis_2023_aerial_imagery/imagefolder-dataset/train/metadata.csv
Selected 50 samples
Loading and resizing images...


/fsx/avijit/anaconda3/envs/py312/lib/python3.12/site-packages/PIL/Image.py:3402: DecompressionBombWarning: Image size (100000000 pixels) exceeds limit of 89478485 pixels, could be decompression bomb DOS attack.
  warnings.warn(


Resizing images...
Saving to /fsx/avijit/projects/datacommonsMA/massgis_2023_aerial_imagery/imagefolder-dataset/data/sample_dataset_256x256.parquet...
Saved sample dataset to /fsx/avijit/projects/datacommonsMA/massgis_2023_aerial_imagery/imagefolder-dataset/data/sample_dataset_256x256.parquet
File size: 6.28 MB
Verifying saved file...
Columns in saved file: ['image', 'tilename', 'zone']
Number of rows: 50


In [24]:
parquet_file = pq.ParquetFile(output_path)
print(parquet_file.metadata)

  created_by: parquet-cpp-arrow version 19.0.0
  num_columns: 4
  num_rows: 50
  num_row_groups: 1
  format_version: 2.6
  serialized_size: 2731
